Information to check
- names
- description
- url
- subjects & keywords
- content type
- repo type
- policies



In [1]:
import ast
import csv
import json

import numpy as np
import pandas as pd

import plotly
from plotly.offline import iplot, init_notebook_mode
import plotly.graph_objs as go
import plotly.express as px

pd.set_option('display.max_columns', None)

## Loading dataset

In [2]:
re3data_df = pd.read_csv('../data/raw/re3data.tsv', delimiter='\t', 
                        converters={'subject': ast.literal_eval,
                                    'keyword': ast.literal_eval,
                                    'additional_name': ast.literal_eval,
                                    'repository_id': ast.literal_eval,
                                    'type': ast.literal_eval,
                                    'content_type': ast.literal_eval,
                                    'provider_type': ast.literal_eval,
                                    'institution': ast.literal_eval
                                    })
re3data_df.head()

openaire_id    re3data_id  \
0  re3data_____::91780fe96da5ba32f804e43359c154ba  r3d100000001   
1  re3data_____::cc3ea05c863cd49af75f7f54e0e86f09  r3d100000002   
2  re3data_____::a2f73fbe91311f4356d0d7957c441773  r3d100000004   
3  re3data_____::0394b97eb11f19785cbca1ec830429da  r3d100000005   
4  re3data_____::a48f09c562b247a9919acfe195549b47  r3d100000006   

                    repository_name  \
0  Odum Institute Archive Dataverse   
1      Access to Archival Databases   
2    Datenbank Gesprochenes Deutsch   
3                     UNC Dataverse   
4          Archaeology Data Service   

                                     additional_name  \
0                                                 []   
1                                              [AAD]   
2  [DGD, DGD2 (formerly), Database for Spoken Ger...   
3           [University of North Carolina Dataverse]   
4                                              [ADS]   

                             repository_url  \
0  https://dataverse.unc.edu/dataverse/odum   
1             https://aad.archives.gov/aad/   
2              https://dgd.ids-mannheim.de/   
3                https://dataverse.unc.edu/   
4     https://archaeologydataservice.ac.uk/   

                                   repository_id  \
0                                             []   
1             [RRID:SCR_010479, RRID:nlx_157752]   
2                                             []   
3                                             []   
4  [FAIRsharing_doi:10.25504/FAIRsharing.hm1mfg]   

                                         description             type  \
0  The Odum Institute Archive Dataverse contains ...   [disciplinary]   
1  You will find in the Access to Archival Databa...   [disciplinary]   
2  The "Database for Spoken German (DGD)" is a co...   [disciplinary]   
3  UNC Dataverse is an open-source repository sof...  [institutional]   
4  The ADS is an accredited digital repository fo...   [disciplinary]   

                                            size update_date  start_date  \
0                  13 dataverses; 3.050 datasets  2020-12-04         NaN   
1                                            NaN         NaN        1985   
2                                     34 corpora  2020-02-03        2012   
3  186 dataverses; 25.272 studies; 229.442 files  2020-11-30        2011   
4                                   1837 results  2020-05-20  1996-10-01   

  end_date                                            subject  \
0      NaN  [1 Humanities and Social Sciences, 111 Social ...   
1      NaN  [1 Humanities and Social Sciences, 102 History...   
2      NaN  [1 Humanities and Social Sciences, 104 Linguis...   
3      NaN  [1 Humanities and Social Sciences, 111 Social ...   
4      NaN  [1 Humanities and Social Sciences, 101 Ancient...   

  mission_statement                                       content_type  \
0            false   [Databases, Plain text, Scientific and statist...   
1             true   [Images, Standard office documents, Structured...   
2             true   [Audiovisual data, Standard office documents, ...   
3             true   [Archived data, Plain text, Raw data, Scientif...   
4             true   [Archived data, Audiovisual data, Databases, I...   

                     provider_type  \
0                   [dataProvider]   
1                   [dataProvider]   
2  [dataProvider, serviceProvider]   
3  [dataProvider, serviceProvider]   
4  [dataProvider, serviceProvider]   

                                             keyword  \
0  [FAIR, Middle East, crime, demography, economy...   
1                                       [US History]   
2  [Australian German, FOLK, German dialects, Pfe...   
3  [FAIR, census, demographic survey, demography,...   
4  [FAIR, archaeology, cultural heritage, prehist...   

                                         institution policy database_access  \
0  [[Odum Institute for Research in Social Scienc...  true            true    
1  [[The U.

In [3]:
re3data_df.columns

Index(['openaire_id', 're3data_id', 'repository_name', 'additional_name',
       'repository_url', 'repository_id', 'description', 'type', 'size',
       'update_date', 'start_date', 'end_date', 'subject', 'mission_statement',
       'content_type', 'provider_type', 'keyword', 'institution', 'policy',
       'database_access', 'database_license', 'data_access', 'data_license',
       'data_upload', 'data_upload_license', 'software', 'versioning', 'api',
       'pid_system', 'citation_guideline_url', 'aid_system',
       'enhanced_publication', 'quality_management', 'certificate',
       'metadata_standard', 'syndication', 'remarks', 'entry_date',
       'last_update'],
      dtype='object')

In [4]:
def empty_list_is_nan(cell):
    if isinstance(cell, list):
        return np.nan if len(cell) == 0 else cell
    else:
        return cell
    
re3data_df = re3data_df.applymap(empty_list_is_nan)

In [5]:
re3data_df.describe(include='all')

openaire_id    re3data_id  \
count                                             2707          2707   
unique                                            2707          2707   
top     re3data_____::4cea5a5ea78542232a51190879756661  r3d100011254   
freq                                                 1             1   

          repository_name additional_name                 repository_url  \
count                2707            2137                           2686   
unique               2704            2128                           2683   
top     EarthChem Library          [IRIS]  http://www.jcvi.org/cms/home/   
freq                    2               2                              2   

             repository_id                                        description  \
count                  829                                               2707   
unique                 828                                               2705   
top     [doi:10.17171/1-6]  The repository is no longer available. >>>!!!<...   
freq                     2                                                  2   

                  type        size update_date start_date end_date  \
count             2677        1260        1248       1762      146   
unique               8        1233         687        351       79   
top     [disciplinary]  2 datasets  2019-05-15       2008     2015   
freq              1713           6          15         92       11   

                                                  subject mission_statement  \
count                                                2685              2707   
unique                                               1367                 2   
top     [1 Humanities and Social Sciences, 2 Life Scie...             true    
freq                                                  222              2286   

                       content_type   provider_type              keyword  \
count                          2700            2699                 2699   
unique                         1323               4                 2474   
top     [Standard office documents]  [dataProvider]  [multidisciplinary]   
freq                             30            1748                  190   

                                              institution policy  \
count                                                2706   2707   
unique                                               2685      2   
top     [[National Center for Biotechnology Informatio...  true    
freq                                                    6   2394   

       database_access database_license data_access data_license data_upload  \
count             2707             2707        2707         2707        2707   
unique               1                2           2            2           2   
top              true            false        true         true        true    
freq              2707             2134        2701         2693        2681   

       data_upload_license software versioning     api pid_system  \
count                 2707     2707       1292    2707       2707   
unique                   2        2          2       2          2   
top                 false     true         yes  false       true    
freq                  1988     2227       1086    1485       2448   

       citation_guideline_url aid_system enhanced_publication  \
count                    2707       2707                 2704   
unique                      1          1                    3   
top                     true       true               unknown   
freq                     2707       2707                 1592   

       quality_management certificate metadata_standard syndication  \
count                2705        2707              2707        2707   
unique                  3           2                 2           2   
top                   yes      false             false       false    
freq                 1492        2481              1655        2129  

In [6]:
re3data_df.isna().sum()

openaire_id                  0
re3data_id                   0
repository_name              0
additional_name            570
repository_url              21
repository_id             1878
description                  0
type                        30
size                      1447
update_date               1459
start_date                 945
end_date                  2561
subject                     22
mission_statement            0
content_type                 7
provider_type                8
keyword                      8
institution                  1
policy                       0
database_access              0
database_license             0
data_access                  0
data_license                 0
data_upload                  0
data_upload_license          0
software                     0
versioning                1415
api                          0
pid_system                   0
citation_guideline_url       0
aid_system                   0
enhanced_publication         3
quality_

In [7]:
re3data_df.content_type.explode().unique()

array(['Databases', 'Plain text',
       'Scientific and statistical data formats',
       'Standard office documents', 'other', 'Images', 'Structured text',
       'Audiovisual data', 'Archived data', 'Raw data',
       'Software applications', 'Source code', 'Structured graphics',
       'Configuration data', 'Networkbased data', nan], dtype=object)

In [8]:
re3data_df.provider_type.explode().unique()

array(['dataProvider', 'serviceProvider', nan], dtype=object)